In [ ]:
import requests
from bs4 import BeautifulSoup
import os
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager
import time
from tqdm import tqdm, trange
import pandas as pd
import pyodbc

# Set display options
pd.set_option('display.max_columns', None)  # or specify the exact number of columns you have
pd.set_option('display.max_colwidth', None)  # to show full width of the columns
pd.set_option('display.width', None)  # to auto-detect the width of your terminal
pd.set_option('display.max_rows', None)

In [ ]:
import requests
from bs4 import BeautifulSoup
import pandas as pd

# URL of the webpage
url = 'https://kmdvalg.dk/KV/2021/K84982101.htm'  # Use the actual URL

# Fetch the webpage content
response = requests.get(url)
soup = BeautifulSoup(response.content, 'html.parser')

# Find the section containing the list of links
links_section = soup.find('div', class_='list-group')

# Extract the .htm links and their corresponding names
areas = []
for link in links_section.find_all('a', class_='list-group-item'):
    href = link['href']
    name = link.text.strip()
    areas.append([href, name])

# Convert the list to a DataFrame
df_valgsteder = pd.DataFrame(areas, columns=['Link', 'Area'])

# Display the DataFrame
df_valgsteder.head()


Link         Area
0  K84982101001.htm  1. Østerbro
1  K84982101002.htm      1. Nord
2  K84982101003.htm       1. Syd
3  K84982101005.htm      1. Vest
4  K84982101006.htm  1. Nordvest

In [3]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from tqdm import tqdm

# Base URL for the webpage
base_url = 'https://kmdvalg.dk/KV/2021/'

# Initialize a list to collect all the data
all_data = []

# Loop through each row in df_valgsteder with tqdm for progress tracking
for index, row in tqdm(df_valgsteder.iterrows(), total=df_valgsteder.shape[0]):
    area_name = row['Area']  # Assuming the area name column is labeled 'Area'
    link = row['Link']       # Assuming the link column is labeled 'Link'

    # Modify the link to include 'B' before the .htm
    modified_link = link.replace('.htm', 'B.htm')
    
    full_url = base_url + modified_link
    response = requests.get(full_url)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Find the outer box that contains all candidate data
    outer_boxes = soup.find_all('div', class_='col-xs-12 col-sm-6 col-md-8 col-lg-8 content-block kmd-personal-votes-list')

    for box in outer_boxes:
        # Extract all rows containing candidate names and votes
        rows = box.find_all('div', class_='row table-like-row')

        for row in rows:
            name = row.find('div', class_='col-xs-7').text.strip()
            votes = row.find('div', class_='col-xs-5').text.strip()
            all_data.append([area_name, name, votes])

# Convert the collected data into a DataFrame
df_votes = pd.DataFrame(all_data, columns=['Area', 'Name', 'Votes'])

# Drop the first row
df_votes = df_votes.iloc[1:].reset_index(drop=True)


# Display the DataFrame
print(df_votes)


100%|██████████| 53/53 [00:04<00:00, 11.57it/s]

                  Area                     Name               Votes
0          1. Østerbro             Mia Nyegaard                 119
1          1. Østerbro         Christopher Røhl                  43
2          1. Østerbro  Mette Annelie Rasmussen                 176
3          1. Østerbro    Jes Vissing Tiedemann                  15
4          1. Østerbro        Katrine Kildgaard                  75
5          1. Østerbro           Sally Khallash                  20
6          1. Østerbro      Jino Victoria Doabi                  25
7          1. Østerbro          Dan Kreutzfeldt                   6
8          1. Østerbro            Lartey Lawson                  50
9          1. Østerbro            Emil Moselund                 104
10         1. Østerbro             Kashif Ahmad                  13
11         1. Østerbro      Emil Sloth Andersen                  39
12         1. Østerbro               Kim Mandix                   8
13         1. Østerbro             Hanne Kofoed 

In [4]:
df_votes.to_csv('df_votes_kbh.csv', index=False)

In [6]:
df_votes.head()

Area                     Name Votes
0  1. Østerbro             Mia Nyegaard   119
1  1. Østerbro         Christopher Røhl    43
2  1. Østerbro  Mette Annelie Rasmussen   176
3  1. Østerbro    Jes Vissing Tiedemann    15
4  1. Østerbro        Katrine Kildgaard    75

In [52]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from tqdm import tqdm

# Base URL for the webpage
base_url = 'https://kmdvalg.dk/KV/2021/'

# Initialize a list to collect all the data
all_data = []

# Loop through each row in df_valgsteder with tqdm for progress tracking
for index, row in tqdm(df_valgsteder.iterrows(), total=df_valgsteder.shape[0]):
    area_name = row['Area']  # Assuming the area name column is labeled 'Area'
    link = row['Link']       # Assuming the link column is labeled 'Link'
    
    full_url = base_url + link
    response = requests.get(full_url)
    soup = BeautifulSoup(response.content, 'html.parser')

    # Find the outer box that contains all candidate data
    outer_boxes = soup.find_all('div', class_='col-xs-12 col-sm-6 col-md-8 content-block kmd-parti-list')

    for box in outer_boxes:
        # Extract all rows containing candidate names and votes
        rows = box.find_all('div', class_='row table-like-row')

        for row in rows[2:]:
            # Check if the row contains the header (which we want to skip)
            if row.find('div', class_='table-like-cell col-xs-7 col-sm-6 col-md-4 roboto-bold'):
                continue  # Skip the header row

            parti = row.find('div', class_='table-like-cell col-xs-7 col-sm-6 col-md-4 ').get_text(strip=True)

            # Find stemmetallet
            stemme = row.find('div', class_='table-like-cell col-xs-3 col-sm-4 col-md-2 text-right roboto-bold').get_text(strip=True)
            
            # Find procentdelen
            procent = row.find('div', class_='col-xs-3 no-left-padding progress-bar-counter').get_text(strip=True)
    
            all_data.append([area_name, parti, stemme, procent])

# Convert the collected data into a DataFrame
df_valg = pd.DataFrame(all_data, columns=['Area', 'Party', 'Votes', 'Percentage'])

# Display the DataFrame
print(df_valg.head())


  0%|          | 0/53 [00:00<?, ?it/s]


AttributeError: 'NoneType' object has no attribute 'get_text'

In [50]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from tqdm import tqdm

# Base URL for the webpage
base_url = 'https://kmdvalg.dk/KV/2021/'

# Initialize a list to collect all the data
all_data = []

# Loop through each row in df_valgsteder with tqdm for progress tracking
for index, row in tqdm(df_valgsteder.iterrows(), total=df_valgsteder.shape[0]):
    area_name = row['Area']  # Assuming the area name column is labeled 'Area'
    link = row['Link']       # Assuming the link column is labeled 'Link'
    
    full_url = base_url + link
    response = requests.get(full_url)
    soup = BeautifulSoup(response.content, 'html.parser')
    print(f"Fetching data from: {full_url}")
    
    # Find the outer box that contains all candidate data
    outer_boxes = soup.find_all('div', class_='col-xs-12 col-sm-6 col-md-8 content-block kmd-parti-list')

    for box in outer_boxes:
        # Extract all rows containing candidate names and votes
        rows = box.find_all('div', class_='row table-like-row')

        for row in rows:
            #party = row.find('span', class_='parti-letter').text.strip()
            #print(party)
            #name = row.find('a').text.strip()
            votes = row.find('div', class_='table-like-cell col-xs-3 col-sm-4 col-md-2 text-right roboto-bold').text.strip()
            print(votes)
            vote_change = row.find('div', class_='table-like-cell no-left-padding col-xs-2 col-sm-2 col-md-1 text-right roboto-bold').text.strip()
            percentage = row.find('div', class_='progress-bar-counter').text.strip()
            percentage_change = row.find_all('div', class_='table-like-cell no-left-padding col-xs-2 col-sm-2 col-md-1 text-right roboto-bold')[-1].text.strip()

            data.append({
                'Party': party,
                'Name': name,
                'Votes': votes,
                'Vote Change': vote_change,
                'Percentage': percentage,
                'Percentage Change': percentage_change,
            })

# Convert the collected data into a DataFrame
df_votes = pd.DataFrame(all_data, columns=['Area', 'Name', 'Votes'])

# Display the DataFrame
print(df_votes)


  0%|          | 0/53 [00:01<?, ?it/s]

Fetching data from: https://kmdvalg.dk/KV/2021/K84982101001.htm


AttributeError: 'NoneType' object has no attribute 'text'

In [37]:
print(box)

<div class="col-xs-12 col-sm-6 col-md-8 content-block kmd-parti-list"> <div class="content-block-header">                    Kandidatlister                    <span class="content-block-sub-header"> - Klik på partiet og se fordelingen af personlige stemmer.</span> </div> <!--table-header--> <div class="row table-like-row"> <div class="table-like-cell col-xs-7 col-sm-6 col-md-4 roboto-bold">Kandidatlister</div> <div class="table-like-cell col-xs-3 col-sm-4 col-md-2 roboto-bold text-right">Stemmetal</div> <div class="table-like-cell no-left-padding col-xs-2 col-sm-2 col-md-1 roboto-bold text-right">(+/-)</div> <div class="table-like-cell col-xs-10 col-sm-10 col-md-4 hidden-xs hidden-sm roboto-bold">Procenter</div> <div class="table-like-cell no-left-padding col-xs-2 col-sm-2 col-md-1 hidden-xs hidden-sm roboto-bold text-right">(+/-)</div> </div> <!--table-content--> <div class="row table-like-row">
<div class="table-like-cell col-xs-7 col-sm-6 col-md-4"><span class="parti-letter">A</span

In [64]:
import requests
from bs4 import BeautifulSoup

# Antag at 'html_content' indeholder den HTML-kode du har sendt.
# Hvis du får HTML'en fra en webside, kan du bruge requests til at hente den:
# response = requests.get("URL_TIL_DIN_WEBSITE")
# html_content = response.content

html_content = """
https://kmdvalg.dk/KV/2021/K84982101001.htm
"""

full_url = 'https://kmdvalg.dk/KV/2021/K84982101001.htm'
response = requests.get(full_url)
soup = BeautifulSoup(response.content, 'html.parser')

# Find alle rækker, der indeholder partier
rows = soup.find_all('div', class_='row table-like-row')

# Initialiser en liste til at gemme dataene
data = []

# Gennemgå hver række og udtræk relevant information
for row in rows:
    print(row.prettify())  # Udskriv hele strukturen af 'row' for at se, hvad der findes

    # Prøv en mere generel søgning efter div med "col-xs-7"
    parti_div = row.find('div', class_='col-xs-7')
    if parti_div:
        print("Parti div fundet:", parti_div.prettify())
    else:
        print("Parti div ikke fundet i denne row.")

<div class="row table-like-row">
 <div class="table-like-cell col-xs-7 col-sm-6 col-md-4 roboto-bold">
  Kandidatlister
 </div>
 <div class="table-like-cell col-xs-3 col-sm-4 col-md-2 roboto-bold text-right">
  Stemmetal
 </div>
 <div class="table-like-cell no-left-padding col-xs-2 col-sm-2 col-md-1 roboto-bold text-right">
  (+/-)
 </div>
 <div class="table-like-cell col-xs-10 col-sm-10 col-md-4 hidden-xs hidden-sm roboto-bold">
  Procenter
 </div>
 <div class="table-like-cell no-left-padding col-xs-2 col-sm-2 col-md-1 hidden-xs hidden-sm roboto-bold text-right">
  (+/-)
 </div>
</div>

Parti div fundet: <div class="table-like-cell col-xs-7 col-sm-6 col-md-4 roboto-bold">
 Kandidatlister
</div>

<div class="row table-like-row">
 <div class="table-like-cell col-xs-7 col-sm-6 col-md-4">
  <span class="parti-letter">
   A
  </span>
  <a href="k84982101001A.htm">
   Socialdemokratiet
  </a>
 </div>
 <div class="table-like-cell col-xs-3 col-sm-4 col-md-2 text-right roboto-bold">
  1.321
 <

In [63]:
print(data)

[]


In [5]:
# Filter the DataFrame for Emil Moselund
emil_df = df_votes[df_votes['Name'] == 'Emil Moselund']
# Ensure that the 'Votes' column is numeric
emil_df['Votes'] = pd.to_numeric(emil_df['Votes'], errors='coerce')



C:\Users\misc\AppData\Local\Temp\ipykernel_42812\1438257205.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  emil_df['Votes'] = pd.to_numeric(emil_df['Votes'], errors='coerce')


In [6]:
import geopandas as gpd
import pandas as pd

# GeoJSON URL
geojson_url = "https://wfs-kbhkort.kk.dk/k101/ows?service=WFS&version=1.0.0&request=GetFeature&typeName=k101:afstemningsomraade&outputFormat=json&SRSNAME=EPSG:4326"
gdf = gpd.read_file(geojson_url)

# Ensure names match correctly
emil_df['Area'] = emil_df['Area'].str.strip()
gdf['navn'] = gdf['navn'].str.strip()

# Merge the filtered DataFrame with the GeoDataFrame
merged_emil_gdf = pd.merge(emil_df, gdf, left_on='Area', right_on='navn')

# Convert the merged DataFrame to a GeoDataFrame
merged_emil_gdf = gpd.GeoDataFrame(merged_emil_gdf, geometry='geometry').dropna(subset=['geometry'])


C:\Users\misc\AppData\Local\Temp\ipykernel_42812\3690656721.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  emil_df['Area'] = emil_df['Area'].str.strip()


In [7]:
#merged_emil_gdf.head()

In [1]:
import folium
from folium import Choropleth

# Create a Folium map centered on Copenhagen
m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

# Create a Choropleth map for Emil Moselund's votes
Choropleth(
    geo_data=merged_emil_gdf,
    name='choropleth',
    data=merged_emil_gdf,
    columns=['Area', 'Votes'],
    key_on='feature.properties.navn',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Votes for Emil Moselund',
).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save and display the map
m.save('emil_moselund_votes.html')
m


NameError: name 'merged_emil_gdf' is not defined

In [ ]:
# Create a Folium map centered on Copenhagen
m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

# Add a Choropleth map for Emil Moselund's votes
Choropleth(
    geo_data=merged_emil_gdf,
    name='choropleth',
    data=merged_emil_gdf,
    columns=['navn', 'Votes'],  # 'navn' must match the key used in GeoJSON
    key_on='feature.properties.navn',
    fill_color='YlGn',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Votes for Emil Moselund',
).add_to(m)

# Add areas with popups
for _, row in merged_emil_gdf.iterrows():
    # Create a GeoJson layer with a popup
    folium.GeoJson(
        row['geometry'],
        style_function=lambda x: {'fillColor': '#PuRd', 'color': 'transparent', 'weight': 0},  # Remove borders
        popup=folium.Popup(f"Area: {row['Area']}<br>Votes: {row['Votes']}", max_width=300),
        tooltip=row['Area']
    ).add_to(m)

# Add layer control
folium.LayerControl().add_to(m)

# Save and display the map
m.save('emil_moselund_votes_choropleth_popup.html')
m

In [ ]:
df_votes.head()

Area                     Name Votes
0  1. Østerbro             Mia Nyegaard   119
1  1. Østerbro         Christopher Røhl    43
2  1. Østerbro  Mette Annelie Rasmussen   176
3  1. Østerbro    Jes Vissing Tiedemann    15
4  1. Østerbro        Katrine Kildgaard    75

In [ ]:
import geopandas as gpd
import pandas as pd
import folium
import ipywidgets as widgets
from IPython.display import display
from folium import Choropleth

# GeoJSON URL
geojson_url = "https://wfs-kbhkort.kk.dk/k101/ows?service=WFS&version=1.0.0&request=GetFeature&typeName=k101:afstemningsomraade&outputFormat=json&SRSNAME=EPSG:4326"
gdf = gpd.read_file(geojson_url)

# Ensure names match correctly
df_votes['Area'] = df_votes['Area'].str.strip()
gdf['navn'] = gdf['navn'].str.strip()

# Merge DataFrame with GeoDataFrame
merged_gdf = pd.merge(df_votes, gdf, left_on='Area', right_on='navn')
merged_gdf = gpd.GeoDataFrame(merged_gdf, geometry='geometry').dropna(subset=['geometry'])

# Create a function to update the map
def update_map(candidate_name):
    # Filter for the selected candidate
    candidate_df = merged_gdf[merged_gdf['Name'] == candidate_name]
    
    # Ensure 'Votes' is numeric
    candidate_df['Votes'] = pd.to_numeric(candidate_df['Votes'], errors='coerce')

    # Create a Folium map centered on Copenhagen
    m = folium.Map(location=[55.6761, 12.5683], zoom_start=12)

    # Add a Choropleth map for the selected candidate's votes
    Choropleth(
    geo_data=candidate_df,
    name='choropleth',
    data=candidate_df,
    columns=['navn', 'Votes'],
    key_on='feature.properties.navn',
    fill_color='PuRd',
    fill_opacity=0.7,
    line_opacity=0,  # Set line_opacity to 0
    line_weight=0,   # Set line_weight to 0 to remove borders
    bins=[0, 20, 40, 60, 80, 100, 120, 140, 160, 180],
    legend_name=f'Votes for {candidate_name}',
).add_to(m)

    for _, row in candidate_df.iterrows():
        folium.GeoJson(
            row['geometry'],
            style_function=lambda x: {'fillColor': '#PuRd', 'color': 'transparent', 'weight': 0},  # Remove borders
            popup=folium.Popup(f"Area: {row['Area']}<br>Votes: {row['Votes']}", max_width=300),
            tooltip=row['Area']
        ).add_to(m)

    # Add layer control
    folium.LayerControl().add_to(m)
    
    # Display the map
    return m

# Create a dropdown widget
candidate_names = df_votes['Name'].unique()
dropdown = widgets.Dropdown(options=candidate_names, description='Candidate:')

# Display the initial map
initial_map = update_map(candidate_names[0])
display(initial_map)

# Define a callback function for the dropdown
def on_value_change(change):
    display(update_map(change['new']))

# Attach the callback to the dropdown widget
dropdown.observe(on_value_change, names='value')

# Display the dropdown
display(dropdown)


c:\Python311\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


Dropdown(description='Candidate:', options=('Mia Nyegaard', 'Christopher Røhl', 'Mette Annelie Rasmussen', 'Je…

c:\Python311\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
